For this assignment, you will be required to explore and cluster the neighborhoods in Toronto.

# Question 1: Processing

In [1]:
#Install relevant libraries for scraping

!pip install bs4
!pip install requests

from bs4 import BeautifulSoup
import requests
import pandas as pd
pd.set_option('display.max_rows', 500)

/opt/conda/envs/Python-3.7-OpenCE/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-OpenCE/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
  Created wheel for bs4: filename=bs4-0.0.1-py3-none-any.whl size=1273 sha256=f74e6bf9b8229cf92c3da0b5ff9e070e5b707e57688e3d197a4f1c93775f28bf
  Stored in directory: /tmp/wsuser/.cache/pip/wheels/0a/9e/ba/20e5bbc1afef3a491f0b3bb74d508f99403aabe76eda2167ca
Successfully built bs4
/opt/conda/envs/Python-3.7-OpenCE/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/opt/conda/envs/Python-3.7-OpenCE/lib/

In [2]:
#URL of Toronto Wiki.
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"

# Get the contents of the webpage and store in a variable called data
data  = requests.get(url).text
soup = BeautifulSoup(data,"html5lib")

tables = soup.find_all('table', rules="all")

In [3]:
#Create dataframe from contents of webpage
toronto_data = pd.DataFrame(columns=["PostalCode", "Combined"])

for row in tables[0].tbody.find_all("tr"):
    for col in row.find_all("td"):
        postal = col.find('br').previousSibling
        span = col.find_all("span")
        
        PostalCode = postal
        Combined = span[0].text.strip().strip(')').replace(' /',',').replace(')',' ').strip(' ')
        toronto_data = toronto_data.append({"PostalCode":PostalCode, "Combined":Combined}, ignore_index=True)
        
toronto_data.head()

PostalCode                                    Combined
0        M1A                                Not assigned
1        M2A                                Not assigned
2        M3A                        North York(Parkwoods
3        M4A                 North York(Victoria Village
4        M5A  Downtown Toronto(Regent Park, Harbourfront

In [4]:
#Processing

#Remove 'Not Assigned'
toronto_data = toronto_data[~(toronto_data['Combined'].str.contains("Not"))]

#Remove 'Split Cells to create Borough and Neighborhood Columns'
splitData = toronto_data["Combined"].str.split("(", n=1, expand=True)
toronto_data["Borough"] = splitData[0]
toronto_data["Neighborhood"] = splitData[1].str.strip(")")

In [5]:
#Cleaning data and resetting index
toronto_data.drop(columns=['Combined'], inplace=True)
toronto_data.reset_index(drop=True, inplace=True)
toronto_data['Borough']=toronto_data['Borough'].replace({'Downtown TorontoStn A PO Boxes25 The Esplanade':'Downtown Toronto Stn A',
                                             'East TorontoBusiness reply mail Processing Centre969 Eastern':'East Toronto Business',
                                             'EtobicokeNorthwest':'Etobicoke Northwest','East YorkEast Toronto':'East York/East Toronto',
                                             'MississaugaCanada Post Gateway Processing Centre':'Mississauga'})
toronto_data['Neighborhood']=toronto_data['Neighborhood'].replace({'Don Mills South(Flemingdon Park':'Don Mills South','Downsview East  (CFB Toronto':'Downsview East'})

In [7]:
toronto_data.head()

PostalCode           Borough                      Neighborhood
0        M3A        North York                         Parkwoods
1        M4A        North York                  Victoria Village
2        M5A  Downtown Toronto         Regent Park, Harbourfront
3        M6A        North York  Lawrence Manor, Lawrence Heights
4        M7A      Queen's Park     Ontario Provincial Government

In [6]:
toronto_data.shape

(103, 3)

-----

-----

# Question 2: Combining Geolocation

In [8]:
# The code was removed by Watson Studio for sharing.

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [12]:
#Combining both dataframes

merged_df = df_data_1.merge(toronto_data, how = 'inner', on = ['PostalCode'])
merged_toronto = merged_df[['PostalCode', 'Borough', 'Neighborhood', 'Latitude', 'Longitude']]
merged_toronto.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

-----

-----

# Question 3: Exploring

In [13]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # transform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python-3.7-OpenCE

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2021.5.30          |   py37h89c1867_0         141 KB  conda-forge
    geographiclib-1.52         |     pyhd8ed1ab_0          35 KB  conda-forge
    geopy-2.2.0                |     pyhd8ed1ab_0          67 KB  conda-forge
    python_abi-3.7             |          2_cp37m           4 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         247 KB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.52-pyhd8ed1ab_0
  geopy              conda-forge/noarch::geopy-2.2.0-pyhd8ed1ab_0
  python_abi         conda-forge/linux-64::python_abi-3.7-2_cp37m

The following p

In [14]:
#Foursquare ID
CLIENT_ID = 'PIV2E4X2OJWZQJ00IB455JQOXFD5KFUS3VY0Y2R4UQKX1K0S' # your Foursquare ID
CLIENT_SECRET = '4BK5A5YXELWV5ZI422OCNQJY00V1HHUAGHI4410TYDBQIVDF' # your Foursquare Secret
ACCESS_TOKEN = 'AMBMRA2KLUF0P5CMZGRIBZ3V3B2JMGTJ4JP0DOM0Q0GHITHC' # your FourSquare Access Token
VERSION = '20180604'
LIMIT = 30

In [15]:
#Get Toronto's coords
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [21]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(merged_toronto['Latitude'], merged_toronto['Longitude'], merged_toronto['Borough'], merged_toronto['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

-----

-----

# Question 3: Clustering

In [84]:
#Function to get information from foursquare on all Toronto neighborhoods
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
#         print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [85]:
# Get all toronto venues
toronto_venues = getNearbyVenues(names=merged_toronto['Neighborhood'],
                                   latitudes=merged_toronto['Latitude'],
                                   longitudes=merged_toronto['Longitude']
                                  )

In [86]:
print(toronto_venues.shape)
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

(1337, 7)
There are 237 uniques categories.


In [87]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                          Malvern, Rouge              43.806686   
1  Rouge Hill, Port Union, Highland Creek              43.784535   
2  Rouge Hill, Port Union, Highland Creek              43.784535   
3       Guildwood, Morningside, West Hill              43.763573   
4       Guildwood, Morningside, West Hill              43.763573   

   Neighborhood Longitude                   Venue  Venue Latitude  \
0              -79.194353                 Wendy’s       43.807448   
1              -79.160497  Chris Effects Painting       43.784343   
2              -79.160497   Royal Canadian Legion       43.782533   
3              -79.188711          RBC Royal Bank       43.766790   
4              -79.188711       G & G Electronics       43.765309   

   Venue Longitude              Venue Category  
0       -79.199056        Fast Food Restaurant  
1       -79.163742  Construction & Landscaping  
2       -79.163085                         Bar  
3       -79.191151                        Bank  
4       -79.191537           Electronics Store

In [101]:
# one hot encoding for venue categories
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()

toronto_grouped.head()

Neighborhood  Yoga Studio  \
0                                        Agincourt          0.0   
1                           Alderwood, Long Branch          0.0   
2  Bathurst Manor, Wilson Heights, Downsview North          0.0   
3                                  Bayview Village          0.0   
4                Bedford Park, Lawrence Manor East          0.0   

   Accessories Store  Adult Boutique  Airport  Airport Food Court  \
0                0.0             0.0      0.0                 0.0   
1                0.0             0.0      0.0                 0.0   
2                0.0             0.0      0.0                 0.0   
3                0.0             0.0      0.0                 0.0   
4                0.0             0.0      0.0                 0.0   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0           0.0             0.0              0.0               0.0   
1           0.0             0.0              0.0               0.0   
2           0.0             0.0              0.0               0.0   
3           0.0             0.0              0.0               0.0   
4           0.0             0.0              0.0               0.0   

   American Restaurant  Antique Shop  Art Gallery  Art Museum  \
0                 0.00           0.0          0.0         0.0   
1                 0.00           0.0          0.0         0.0   
2                 0.00           0.0          0.0         0.0   
3                 0.00           0.0          0.0         0.0   
4                 0.04           0.0          0.0         0.0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                  0.0               0.0                 0.0          0.0   
1                  0.0               0.0                 0.0          0.0   
2                  0.0               0.0                 0.0          0.0   
3                  0.0               0.0                 0.0          0.0   
4                  0.0               0.0                 0.0          0.0   

   Auto Workshop  BBQ Joint  Baby Store  Bakery      Bank  Bar  \
0            0.0        0.0         0.0     0.0  0.000000  0.0   
1            0.0        0.0         0.0     0.0  0.000000  0.0   
2            0.0        0.0         0.0     0.0  0.090909  0.0   
3            0.0        0.0         0.0     0.0  0.250000  0.0   
4            0.0        0.0         0.0     0.0  0.000000  0.0   

   Baseball Field  Basketball Court  Basketball Stadium  Beer Bar  Beer Store  \
0             0.0               0.0                 0.0       0.0         0.0   
1             0.0               0.0                 0.0       0.0         0.0   
2             0.0               0.0                 0.0       0.0         0.0   
3             0.0               0.0                 0.0       0.0         0.0   
4             0.0               0.0                 0.0       0.0         0.0   

   Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                 0.0        0.0     0.0            0.0        0.0       0.0   
1                 0.0        0.0     0.0            0.0        0.0       0.0   
2                 0.0        0.0     0.0            0.0        0.0       0.0   
3                 0.0        0.0     0.0            0.0        0.0       0.0   
4                 0.0        0.0     0.0            0.0        0.0       0.0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Burger Joint  \
0             0.2      0.0     0.000000              0.0           0.0   
1             0.0      0.0     0.000000              0.0           0.0   
2             0.0      0.0     0.045455              0.0           0.0   
3             0.0      0.0     0.000000              0.0           0.0   
4             0.0      0.0     0.000000              0.0           0.0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Butcher  Café  \
0            0.0       0.0          0.0       0.0     0.00  0.00   

In [102]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt                Lounge   
1                           Alderwood, Long Branch           Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                  Bank   
3                                  Bayview Village                  Café   
4                Bedford Park, Lawrence Manor East        Sandwich Place   

  2nd Most Common Venue 3rd Most Common Venue      4th Most Common Venue  \
0        Breakfast Spot        Clothing Store  Latin American Restaurant   
1                   Gym                   Pub               Skating Rink   
2           Coffee Shop           Pizza Place              Deli / Bodega   
3    Chinese Restaurant                  Bank        Japanese Restaurant   
4           Coffee Shop    Italian Restaurant                   Pharmacy   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0          Skating Rink      Department Store     Electronics Store   
1        Sandwich Place           Coffee Shop               Dog Run   
2      Sushi Restaurant           Supermarket           Bridal Shop   
3      Department Store           Escape Room     Electronics Store   
4                   Pub             Juice Bar               Butcher   

         8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0  Eastern European Restaurant             Drugstore             Donut Shop  
1                   Donut Shop   Distribution Center           Dance Studio  
2                        Diner         Shopping Mall         Sandwich Place  
3  Eastern European Restaurant             Drugstore             Donut Shop  
4         Fast Food Restaurant                  Café      Indian Restaurant

In [103]:
# set number of clusters
kclusters = 4

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 0], dtype=int32)

In [104]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_venues

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged

Neighborhood  \
0                                        Malvern, Rouge   
1                Rouge Hill, Port Union, Highland Creek   
2                Rouge Hill, Port Union, Highland Creek   
3                     Guildwood, Morningside, West Hill   
4                     Guildwood, Morningside, West Hill   
5                     Guildwood, Morningside, West Hill   
6                     Guildwood, Morningside, West Hill   
7                     Guildwood, Morningside, West Hill   
8                     Guildwood, Morningside, West Hill   
9                     Guildwood, Morningside, West Hill   
10                    Guildwood, Morningside, West Hill   
11                    Guildwood, Morningside, West Hill   
12                                               Woburn   
13                                               Woburn   
14                                               Woburn   
15                                               Woburn   
16                                            Cedarbrae   
17                                            Cedarbrae   
18                                            Cedarbrae   
19                                            Cedarbrae   
20                                            Cedarbrae   
21                                            Cedarbrae   
22                                            Cedarbrae   
23                                            Cedarbrae   
24                                  Scarborough Village   
25                                  Scarborough Village   
26          Kennedy Park, Ionview, East Birchmount Park   
27          Kennedy Park, Ionview, East Birchmount Park   
28          Kennedy Park, Ionview, East Birchmount Park   
29          Kennedy Park, Ionview, East Birchmount Park   
30                      Golden Mile, Clairlea, Oakridge   
31                      Golden Mile, Clairlea, Oakridge   
32                      Golden Mile, Clairlea, Oakridge   
33                      Golden Mile, Clairlea, Oakridge   
34                      Golden Mile, Clairlea, Oakridge   
35                      Golden Mile, Clairlea, Oakridge   
36                      Golden Mile, Clairlea, Oakridge   
37                      Golden Mile, Clairlea, Oakridge   
38                      Golden Mile, Clairlea, Oakridge   
39                      Golden Mile, Clairlea, Oakridge   
40      Cliffside, Cliffcrest, Scarborough Village West   
41      Cliffside, Cliffcrest, Scarborough Village West   
42      Cliffside, Cliffcrest, Scarborough Village West   
43                          Birch Cliff, Cliffside West   
44                          Birch Cliff, Cliffside West   
45                          Birch Cliff, Cliffside West   
46                          Birch Cliff, Cliffside West   
47    Dorset Park, Wexford Heights, Scarborough Town...   
48    Dorset Park, Wexford Heights, Scarborough Town...   
49    Dorset Park, Wexford Heights, Scarborough Town...   
50    Dorset Park, Wexford Heights, Scarborough Town...   
51    Dorset Park, Wexford Heights, Scarborough Town...   
52    Dorset Park, Wexford Heights, Scarborough Town...   
53                                    Wexford, Maryvale   
54                                    Wexford, Maryvale   
55                                    Wexford, Maryvale   
56                                    Wexford, Maryvale   
57                                    Wexford, Maryvale   
58                                            Agincourt   
59                                            Agincourt   
60                                            Agincourt   
61                                            Agincourt   
62                                            Agincourt   
63              Clarks Corners, Tam O'Shanter, Sullivan   
64              Clarks Corners, Tam O'Shanter, Sullivan   
65              Clarks Corners, Tam O'Shanter, Sullivan   
66              Clarks Corners, Tam O'Shanter, Sullivan   
67              Clarks Corners,

In [105]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Looking for neighborhoods in the biggest cluster with Gym as 1st Most Common Venue

In [135]:
tor = toronto_merged.loc[(toronto_merged['Cluster Labels'] == 1) & (toronto_merged['1st Most Common Venue'].str.contains('Gym')), toronto_merged.columns[[0] + list(range(7, toronto_merged.shape[1]))]]
tor.drop_duplicates(subset=['Neighborhood'], inplace=True)
tor.sort_values(by=['1st Most Common Venue'])

Neighborhood  Cluster Labels 1st Most Common Venue  \
178       Don Mills North               1                   Gym   
183       Don Mills South               1                   Gym   
1304        Humber Summit               1                   Gym   
243   Downsview Northwest               1  Gym / Fitness Center   
414      Davisville North               1  Gym / Fitness Center   
1241       Enclave of M4L               1  Gym / Fitness Center   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
178   Caribbean Restaurant          Dessert Shop   Japanese Restaurant   
183             Restaurant           Coffee Shop             Bike Shop   
1304           Pizza Place          Home Service          Dance Studio   
243     Athletics & Sports          Liquor Store        Discount Store   
414                  Hotel        Breakfast Spot     Food & Drink Shop   
1241                   Spa         Auto Workshop               Brewery   

     5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
178                   Café                 Concert Hall      Department Store   
183            Art Gallery           Dim Sum Restaurant           Supermarket   
1304     Electronics Store  Eastern European Restaurant             Drugstore   
243          Grocery Store           Airport Food Court  Colombian Restaurant   
414       Department Store               Sandwich Place                  Park   
1241         Burrito Place                   Comic Shop        Farmers Market   

     8th Most Common Venue        9th Most Common Venue  \
178      Electronics Store  Eastern European Restaurant   
183         Sandwich Place               Discount Store   
1304            Donut Shop                      Dog Run   
243     Falafel Restaurant                  Event Space   
414           Concert Hall                 Dessert Shop   
1241  Fast Food Restaurant                       Garden   

           10th Most Common Venue  
178                     Drugstore  
183              Asian Restaurant  
1304          Distribution Center  
243                   Escape Room  
414   Eastern European Restaurant  
1241                Garden Center